In [1]:
import sys
sys.path.append('third_party/Matcha-TTS')
from cosyvoice.cli.cosyvoice import CosyVoice, CosyVoice2
from cosyvoice.utils.file_utils import load_wav
import torchaudio
import IPython.display as ipd

# cosyvoice = CosyVoice2('pretrained_models/CosyVoice2-0.5B', load_jit=False, load_trt=False, fp16=False)
cosyvoice = CosyVoice2('/data/minju/TTS/CosyVoice_flow_cache/pretrained_models/CosyVoice2-0.5B-long-24k', load_jit=False, load_trt=False, fp16=False)
# cosyvoice = CosyVoice('pretrained_models/CosyVoice-300M-emo', load_jit=True, load_trt=True, fp16=False)
# cosyvoice = CosyVoice('pretrained_models/CosyVoice-300M-emo-flow', load_jit=True, load_trt=True, fp16=False)
# cosyvoice = CosyVoice('./pretrained_models/CosyVoice-300M',load_jit=False, load_trt=False,fp16=False)
# cosyvoice = CosyVoice('./pretrained_models/CosyVoice-300M-long-final',load_jit=True, load_trt=True,fp16=False)
# cosyvoice = CosyVoice('./pretrained_models/CosyVoice-300M-25Hz',load_jit=False, load_trt=False,fp16=False)

2025-04-16 13:19:48,670 - modelscope - INFO - PyTorch version 2.0.0 Found.
2025-04-16 13:19:48,672 - modelscope - INFO - Loading ast index from /root/.cache/modelscope/ast_indexer
2025-04-16 13:19:48,793 - modelscope - INFO - Loading done! Current index file version is 1.15.0, with md5 13b7082244438de82b16012a4fd7baad and a total number of 980 components indexed


failed to import ttsfrd, use WeTextProcessing instead


/data/minju/conda/envs/cosyvoice/lib/python3.10/site-packages/diffusers/models/lora.py:393: FutureWarning: `LoRACompatibleLinear` is deprecated and will be removed in version 1.0.0. Use of `LoRACompatibleLinear` is deprecated. Please switch to PEFT backend by installing PEFT: `pip install peft`.
  deprecate("LoRACompatibleLinear", "1.0.0", deprecation_message)
2025-04-16 13:19:55,258 INFO input frame rate=25
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
/data/minju/conda/envs/cosyvoice/lib/python3.10/site-packages/onnxruntime/capi/onnxruntime_inference_collection.py:115: UserWarning: Specified provider 'CUDAExecutionProvider' is not in available provider names.Available providers: 'AzureExecutionProvider, CPUExecutionProvider'
  warnings.warn(
2025-04-16 13:20:01,707 WETEXT INFO building fst for zh_

In [2]:
cosyvoice.model.flow.encoder.static_chunk_size

50

In [7]:
import torch

flow = torch.load('/data/minju/TTS/CosyVoice_origin/pretrained_models/CosyVoice-300M-long-final/flow.pt')
flow_epoch = flow['epoch']
print(flow['epoch'])

llm = torch.load('/data/minju/TTS/CosyVoice_origin/pretrained_models/CosyVoice-300M-long-final/llm.pt')
print(llm['epoch'])

10
10


In [26]:
cosyvoice.model.flow

MaskedDiffWithXvec(
  (input_embedding): Embedding(4096, 512)
  (spk_embed_affine_layer): Linear(in_features=192, out_features=80, bias=True)
  (encoder): ConformerEncoder(
    (embed): LinearNoSubsampling(
      (out): Sequential(
        (0): Linear(in_features=512, out_features=512, bias=True)
        (1): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
        (2): Dropout(p=0.1, inplace=False)
      )
      (pos_enc): EspnetRelPositionalEncoding(
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
    (after_norm): LayerNorm((512,), eps=1e-05, elementwise_affine=True)
    (encoders): ModuleList(
      (0-5): 6 x ConformerEncoderLayer(
        (self_attn): RelPositionMultiHeadedAttention(
          (linear_q): Linear(in_features=512, out_features=512, bias=True)
          (linear_k): Linear(in_features=512, out_features=512, bias=True)
          (linear_v): Linear(in_features=512, out_features=512, bias=True)
          (linear_out): Linear(in_features=512, out_feat

In [7]:
llm = torch.load('/data/minju/TTS/CosyVoice_origin/pretrained_models/CosyVoice-300M-emo-flow/llm.pt')
print(llm['epoch'])

11


In [7]:
from hyperpyyaml import load_hyperpyyaml

config_file = "/data/minju/TTS/CosyVoice/pretrained_models/CosyVoice2-0.5B/cosyvoice2.yaml"

override_dict = {k: None for k in ['llm', 'flow', 'hift'] if k != "llm"}

with open(config_file, 'r') as f:
    configs = load_hyperpyyaml(f, overrides=override_dict)

print(configs)
epoch = 7
model = configs["llm"]
model.load_state_dict(torch.load(f"/data/minju/TTS/CosyVoice/examples/libritts/cosyvoice2/exp/cosyvoice2/llm/torch_ddp/epoch_{epoch}_whole.pt", map_location='cuda'), strict=False)

print(model)
# cosyvoice.model.llm = model.to("cuda")

OSError: Incorrect path_or_model_id: ''. Please provide either the path to a local folder or the repo_id of a model on the Hub.

In [2]:
import torch
print(cosyvoice.list_available_spks())
print(len(cosyvoice.list_available_spks()))

# emb_path = "/data/minju/TTS/CosyVoice/embedding_models/senti-slx/spk2info.pt"
# emb_path = "/data/minju/TTS/CosyVoice_origin/embedding_models/emo-all-slx/spk2info.pt"
# emb_type = emb_path.split("/")[-2]
# spk2info = torch.load(emb_path, map_location = "cuda")
# cosyvoice.frontend.spk2info = spk2info

# print(cosyvoice.list_available_spks())
# print(len(cosyvoice.list_available_spks()))


['中文女', '中文男', '日语男', '粤语女', '英文女', '英文男', '韩语女']
7


In [16]:
new_audio

array([[-1.3098592e-05, -2.5474098e-06,  1.3086861e-05, ...,
         8.1144020e-07, -1.5924394e-06,  3.0181863e-07]], dtype=float32)

In [19]:
print(np.append(new_audio,  np.array([[0.0] * int(22050 * 0.5)], dtype='float32'),axis=1))

[[-1.3098592e-05 -2.5474098e-06  1.3086861e-05 ...  0.0000000e+00
   0.0000000e+00  0.0000000e+00]]


In [11]:
print(np.array([[0.0] * int(22050 * 0.5)]).shape)

(1, 11025)


In [26]:
import numpy as np
def pad_silence(audio, sample_rate=22050, pad_silence=0.5):
    audio = np.append(audio, np.array([[0.0] * int(sample_rate * pad_silence)], dtype='float32'), axis=1) # pad silence
    return audio

In [5]:
import time
import os
import torch
speaker = 'D-H3-F-008'
speaker = 'happycon'
text = "오늘은 대기 정체와 국외 미세먼지까지 유입되면서 공기 질이 나쁘겠는데요."
# text = "오늘 낮까지 중부와 경북 북부에는 비 또는 눈이 오늘 조금 내리겠습니다."
text = "내일 차츰 개갰고 당분간 예년보다 포근한 겨울 날씨가 이어질 전망입니다."
# text = "오늘까지는 아직 경제에 미친 객관적인 영향까지는 확인되지 않은 상황이다."
# text = "yuna_default_1.05<|endofprompt|>시민사회와 학계 원로들은 헌법재판소의 윤석열 대통령 탄핵심판 결론이 어떻게 나오더라도 결과에 승복하고 포용하는 자세가 중요하다고 강조했다."
text = "sehyeok_default<|endofprompt|>기각 의견을 낸 다섯명 중 문형배 이미선 김형두 정정미 재판관은 한 권한대행이 국회에서 선출된 조한창 정계선 마은혁 재판관 후보자의 임명을 보류한 것이 헌법과 법률 위반이라면서도 파면을 정당화하는 사유는 아니라고 판단했다."
# text = "sehyeok_default<|endofprompt|>주요 부문에선 숀 베이커 감독의 저예산 독립영화 아노라가 작품상, 감독상, 여우주연상, 각본상, 편집상을 수상하며 오관왕에 올랐다."
text = "happycon<|endofprompt|>동지였으면 서둘러 비켰어야 하고, 적이었으면 더 서둘러 비켰어야 할 터인데. 같은 쪽으로 걷겠다라 대담한 자인가, 대책이 없는 자인가."
# text = "sunbeacon<|endofprompt|>충청권 메가시티 조성 기반 등 당위성을 모아 대정부 설득 논리를 보완 강화해야 하는 것은 물론, 지자체와 지역 정치권의 초당적 협력을 토대로 사업을 조속히 완성해야 한다는 요구가 높다."
# text = "sunbeacon<|endofprompt|>인생에서 원하는 것을 얻기 위한 첫번째 단계는 내가 무엇을 원하는지 결정하는 것이다."
# text = "happycon<|endofprompt|>바쁜 하루 속에서도 커피 한 잔의 여유를 즐길 줄 아는 사람이 되고 싶다. 뜨거운 커피를 마시며 오늘 하루를 되돌아보고, 새로운 계획을 세우는 시간. 작은 순간이지만, 이 시간이 내게 큰 의미를 준다."
# text = "happycon<|endofprompt|>짧다랗게 짜깁기된 짙다랗고 짜릿한 짜장 라면이 짜증났다."
text = "happycon<|endofprompt|>여행을 떠나 처음 가본 도시에 도착했을 때 느껴지는 설렘과 두근거림은 항상 특별한 기억으로 남는다. 낯선 거리와 풍경을 천천히 걸으며 그곳의 문화와 사람들을 경험하는 과정이야말로 여행의 가장 큰 즐거움이다."
output_path = 'output/250321'
os.makedirs(output_path, exist_ok=True)
total_tensor = []
start = time.time()
for i, j in enumerate(cosyvoice.inference_sft(text, speaker, stream=True)):
    total_tensor.append(j['tts_speech'])
    # torchaudio.save(f"test_{i}.wav", j['tts_speech'], cosyvoice.sample_rate)
end = time.time()
print(end-start)
concatenated_tensor = torch.cat(total_tensor, dim=-1)
torchaudio.save(f"{output_path}/{speaker}_{text[:3]}.wav", concatenated_tensor, cosyvoice.sample_rate)
ipd.Audio(f"{output_path}/{speaker}_{text[:3]}.wav")

  0%|          | 0/1 [00:00<?, ?it/s]2025-04-16 13:24:30,825 INFO synthesis text happycon<|endofprompt|>여행을 떠나 처음 가본 도시에 도착했을 때 느껴지는 설렘과 두근거림은 항상 특별한 기억으로 남는다. 낯선 거리와 풍경을 천천히 걸으며 그곳의 문화와 사람들을 경험하는 과정이야말로 여행의 가장 큰 즐거움이다.


update! happycon<|endofprompt|>여행을 떠나 처음 가본 도시에 도착했을 때 느껴지는 설렘과 두근거림은 항상 특별한 기억으로 남는다. 낯선 거리와 풍경을 천천히 걸으며 그곳의 문화와 사람들을 경험하는 과정이야말로 여행의 가장 큰 즐거움이다.
86


2025-04-16 13:24:36,960 INFO yield speech len 1.84, rtf 3.3341177131818687
2025-04-16 13:24:41,996 INFO yield speech len 2.0, rtf 2.5170761346817017
2025-04-16 13:24:47,503 INFO yield speech len 2.0, rtf 2.752950072288513
2025-04-16 13:24:52,167 INFO yield speech len 2.0, rtf 2.3304604291915894
2025-04-16 13:24:57,464 INFO yield speech len 2.0, rtf 2.647875428199768
2025-04-16 13:25:02,257 INFO yield speech len 2.0, rtf 2.3952484130859375
2025-04-16 13:25:07,188 INFO yield speech len 2.0, rtf 2.464805006980896
2025-04-16 13:25:12,597 INFO yield speech len 2.0, rtf 2.7029240131378174
2025-04-16 13:25:15,745 INFO yield speech len 0.96, rtf 3.2780235012372336
100%|██████████| 1/1 [00:44<00:00, 44.93s/it]

45.02082848548889


In [41]:
import time
import os
import torch
import soundfile as sf
speaker = '英文男'
# speaker = 'chimneycon'
# speaker = 'sehyeok_default'
# speaker = 'boram_default'
# # speaker = 'sunbeacon'
speaker = 'secretary_joy'
text = "오늘은 대기 정체와 국외 미세먼지까지 유입되면서 공기 질이 나쁘겠는데요."
# text = "오늘 낮까지 중부와 경북 북부에는 비 또는 눈이 오늘 조금 내리겠습니다."
# text = "국민의힘은 민주당의 반응을 광주 정신 사유화라고 비판하며 금남로에서 역대 최대 규모의 보수 성향 집회가 열린 것을 재평가해야 한다고 반박했다. 권성동 국민의힘 원내대표는 국회 기자간담회에서 탄핵 반대 집회 자체를 비판할 수는 있어도 광주는 안 된다는 발상은 지역주의와 편가르기 조장이자 반민주적이라고 했다."
# text = "오늘까지는 아직 경제에 미친 객관적인 영향까지는 확인되지 않은 상황이다."
# text = 'I thank President Bush for his service to our nation, as well as the generosity and cooperation he has shown throughout this transition. The words have been spoken during rising tides of prosperity and the still waters of peace.'
text = '韩语女<|endofprompt|>행복은 거창한 것이 아니다. 그것은 우리가 지금 이 순간에 어떻게 집중하느냐에 달려 있다. 행복은 멀리 있지 않다. 바로 여기, 지금 이 순간에도 존재한다.'
# text = '시민사회와 학계 원로들은 헌법재판소의 윤석열 대통령 탄핵심판 결론이 어떻게 나오더라도 결과에 승복하고 포용하는 자세가 중요하다고 강조했다.'
# text = "안녕하세요? 여러분! 오늘은 약물적 치료에 대해 다루겠습니다. 약물적 치료 중 마약성 진통제는 몰핀, 펜터나일, 악시카도운 등이 있습니다."

# text = "경기도민의 절반은 문화공연을 즐기기 위해 서울을 찾고 있는 것으로 나타났다. 경기도의 인구는 1천400만명에 달하지만, 대형 문화예술공간이 부족해 문화 향유 기회가 제한된다는 지적이 나온다. 27일 경기일보 취재를 종합하면 도내에는 경기아트센터를 제외하고는 대형 문화예술공간이 부족한 실정이다. 경기아트센터는 1991년 개관했으나 시설이 낙후되고 공간이 협소해 도민들의 문화예술 수요를 충족하기 어렵다는 지적이 나온다. 반면 서울은 1978년 개관한 세종문화회관과 1988년 개관한 예술의전당 등 대형 공연장이 있어 문화예술 향유의 중심지 역할을 해왔다."
# text = "에밀리아 페레즈로 올해 주요 시상식과 아카데미 여우조연상까지 휩쓴 조이 살다나는 무대에 올라 눈물을 흘리며 엄마를 외쳤다."
# text = "주요 부문에선 숀 베이커 감독의 저예산 독립영화 아노라가 작품상, 감독상, 여우주연상, 각본상, 편집상을 수상하며 오관왕에 올랐다."
text = "잡을 자격이 없는 난, 일시정지를 깰 자격이 없는 난 그저 기다리는게 최선이니까. 천천히, 평온히, 꼭 와라 민영아!"

start = time.time()
output_path = 'output/250307'
os.makedirs(output_path, exist_ok=True)

total_tensor = []
for i, j in enumerate(cosyvoice.inference_sft(text, speaker, stream=False, speed=0.8)):
    audio = j['tts_speech']
    print(audio.shape, audio.dtype)
    audio = audio.cpu().float().numpy()
    print(audio.shape, audio.dtype)
    audio=  pad_silence(audio, 22050, pad_silence = 5)
    print(audio.shape, audio.dtype)

    audio = torch.tensor(audio)
    # sf.write(f"{output_path}/{speaker}_{text[:3]}_{i}.wav", audio, cosyvoice.sample_rate)
    torchaudio.save(f"{output_path}/{speaker}_{text[:3]}_{i}.wav", audio, cosyvoice.sample_rate)
# end = time.time()
# print(end-start)
# concatenated_tensor = torch.cat(total_tensor, dim=-1)
# torchaudio.save(f"{output_path}/{speaker}_{text[:3]}.wav", concatenated_tensor, cosyvoice.sample_rate)
ipd.Audio(f"{output_path}/{speaker}_{text[:3]}_{i}.wav")

  0%|          | 0/1 [00:00<?, ?it/s]2025-03-07 15:26:57,321 INFO synthesis text 잡을 자격이 없는 난, 일시정지를 깰 자격이 없는 난 그저 기다리는게 최선이니까. 천천히, 평온히, 꼭 와라 민영아!


update! 잡을 자격이 없는 난, 일시정지를 깰 자격이 없는 난 그저 기다리는게 최선이니까. 천천히, 평온히, 꼭 와라 민영아!
45


2025-03-07 15:27:01,378 INFO yield speech len 12.945124716553288, rtf 0.3133439721180452
100%|██████████| 1/1 [00:04<00:00,  4.07s/it]

torch.Size([1, 285440]) torch.float32
(1, 285440) float32
(1, 395690) float32


In [11]:
import time
import os
speaker = '英文男'
# speaker = 'chimneycon'
# speaker = 'sehyeok_default'
# speaker = 'boram_default'
# # speaker = 'sunbeacon'
speaker = 'secretary_joy'
text = "오늘은 대기 정체와 국외 미세먼지까지 유입되면서 공기 질이 나쁘겠는데요."
# text = "오늘 낮까지 중부와 경북 북부에는 비 또는 눈이 오늘 조금 내리겠습니다."
# text = "국민의힘은 민주당의 반응을 광주 정신 사유화라고 비판하며 금남로에서 역대 최대 규모의 보수 성향 집회가 열린 것을 재평가해야 한다고 반박했다. 권성동 국민의힘 원내대표는 국회 기자간담회에서 탄핵 반대 집회 자체를 비판할 수는 있어도 광주는 안 된다는 발상은 지역주의와 편가르기 조장이자 반민주적이라고 했다."
# text = "오늘까지는 아직 경제에 미친 객관적인 영향까지는 확인되지 않은 상황이다."
# text = 'I thank President Bush for his service to our nation, as well as the generosity and cooperation he has shown throughout this transition. The words have been spoken during rising tides of prosperity and the still waters of peace.'
text = '韩语女<|endofprompt|>행복은 거창한 것이 아니다. 그것은 우리가 지금 이 순간에 어떻게 집중하느냐에 달려 있다. 행복은 멀리 있지 않다. 바로 여기, 지금 이 순간에도 존재한다.'
# text = '시민사회와 학계 원로들은 헌법재판소의 윤석열 대통령 탄핵심판 결론이 어떻게 나오더라도 결과에 승복하고 포용하는 자세가 중요하다고 강조했다.'
# text = "안녕하세요? 여러분! 오늘은 약물적 치료에 대해 다루겠습니다. 약물적 치료 중 마약성 진통제는 몰핀, 펜터나일, 악시카도운 등이 있습니다."

# text = "경기도민의 절반은 문화공연을 즐기기 위해 서울을 찾고 있는 것으로 나타났다. 경기도의 인구는 1천400만명에 달하지만, 대형 문화예술공간이 부족해 문화 향유 기회가 제한된다는 지적이 나온다. 27일 경기일보 취재를 종합하면 도내에는 경기아트센터를 제외하고는 대형 문화예술공간이 부족한 실정이다. 경기아트센터는 1991년 개관했으나 시설이 낙후되고 공간이 협소해 도민들의 문화예술 수요를 충족하기 어렵다는 지적이 나온다. 반면 서울은 1978년 개관한 세종문화회관과 1988년 개관한 예술의전당 등 대형 공연장이 있어 문화예술 향유의 중심지 역할을 해왔다."
# text = "에밀리아 페레즈로 올해 주요 시상식과 아카데미 여우조연상까지 휩쓴 조이 살다나는 무대에 올라 눈물을 흘리며 엄마를 외쳤다."
# text = "주요 부문에선 숀 베이커 감독의 저예산 독립영화 아노라가 작품상, 감독상, 여우주연상, 각본상, 편집상을 수상하며 오관왕에 올랐다."
text = "잡을 자격이 없는 난, 일시정지를 깰 자격이 없는 난 그저 기다리는게 최선이니까. 천천히, 평온히, 꼭 와라 민영아!"

start = time.time()
output_path = 'output/250307'
os.makedirs(output_path, exist_ok=True)

total_tensor = []
for i, j in enumerate(cosyvoice.inference_sft(text, speaker, stream=False)):
    total_tensor.append(j['tts_speech'])
    torchaudio.save(f"{output_path}/{speaker}_{text[:3]}_{i}.wav", j['tts_speech'], cosyvoice.sample_rate)
end = time.time()
print(end-start)
concatenated_tensor = torch.cat(total_tensor, dim=-1)
torchaudio.save(f"{output_path}/{speaker}_{text[:3]}.wav", concatenated_tensor, cosyvoice.sample_rate)
ipd.Audio(f"{output_path}/{speaker}_{text[:3]}.wav")

  0%|          | 0/1 [00:00<?, ?it/s]2025-03-07 10:31:18,592 INFO synthesis text 韩语女<|endofprompt|>행복은거창한것이아니다。그것은우리가지금이순간에어떻게집중하느냐에달려있다。행복은멀리있지않다。바로여기,지금이순간에도존재한다。


update! 韩语女<|endofprompt|>행복은거창한것이아니다. 그것은우리가지금이순간에어떻게집중하느냐에달려있다. 행복은멀리있지않다. 바로여기,지금이순간에도존재한다. 
62


2025-03-07 10:31:20,499 INFO yield speech len 1.84, rtf 1.0359931251277095
2025-03-07 10:31:21,804 INFO yield speech len 2.0, rtf 0.6504538059234619
2025-03-07 10:31:22,981 INFO yield speech len 2.0, rtf 0.5870945453643799
2025-03-07 10:31:24,248 INFO yield speech len 2.0, rtf 0.6319773197174072
2025-03-07 10:31:25,686 INFO yield speech len 2.0, rtf 0.7172753810882568
2025-03-07 10:31:27,201 INFO yield speech len 2.0, rtf 0.755948543548584
2025-03-07 10:31:28,071 INFO yield speech len 1.56, rtf 0.5562690588144156
100%|██████████| 1/1 [00:09<00:00,  9.50s/it]

9.525835275650024


In [47]:
import time
import os
speaker = '韩语女'
speaker = 'boram_default'
text = "오늘은 대기 정체와 국외 미세먼지까지 유입되면서 공기 질이 나쁘겠는데요."
# text = "오늘 낮까지 중부와 경북 북부에는 비 또는 눈이 오늘 조금 내리겠습니다."
text = "국민의힘은 민주당의 반응을 광주 정신 사유화라고 비판하며 금남로에서 역대 최대 규모의 보수 성향 집회가 열린 것을 재평가해야 한다고 반박했다. 권성동 국민의힘 원내대표는 국회 기자간담회에서 탄핵 반대 집회 자체를 비판할 수는 있어도 광주는 안 된다는 발상은 지역주의와 편가르기 조장이자 반민주적이라고 했다."
# text = "오늘까지는 아직 경제에 미친 객관적인 영향까지는 확인되지 않은 상황이다."
# text = 'I thank President Bush for his service to our nation, as well as the generosity and cooperation he has shown throughout this transition. The words have been spoken during rising tides of prosperity and the still waters of peace.'
# text = '나는 손으로 우리 마을 쪽 방향을 가리켰다. 우리 마을은, 오리나무들과 가지만 남기고 가지를 모두 전지한 나무들 사이로 보이는 해안가 평지 위에 있었다. 그쪽 방향을 가리켰다. 마을은 여기에서 일키로미터 이상 떨어져 있었다'
# text = '시민사회와 학계 원로들은 헌법재판소의 윤석열 대통령 탄핵심판 결론이 어떻게 나오더라도 결과에 승복하고 포용하는 자세가 중요하다고 강조했다.'
# text = "안녕하세요 여러분. 오늘은 약물적 치료에 대해 다루겠습니다. 약물적 치료 중 마약성 진통제는 몰핀 펜터나일 악시카도운 등이 있습니다."
start = time.time()
total_tensor = []
output_path = 'output/250227-stream'
os.makedirs(output_path, exist_ok=True)
for i, j in enumerate(cosyvoice_long.inference_sft(text, speaker, stream=True)):
    total_tensor.append(j['tts_speech'])
    torchaudio.save(f"{output_path}/long_{speaker}_{text[:3]}_{i}.wav", j['tts_speech'], cosyvoice_long.sample_rate)
end = time.time()
print(end-start)
concatenated_tensor = torch.cat(total_tensor, dim=-1)
torchaudio.save(f"{output_path}/long_{speaker}_{text[:3]}_last.wav", concatenated_tensor, cosyvoice_long.sample_rate)
ipd.Audio(f"{output_path}/long_{speaker}_{text[:3]}_last.wav")

  0%|          | 0/2 [00:00<?, ?it/s]2025-02-27 13:38:00,781 INFO synthesis text 국민의힘은 민주당의 반응을 광주 정신 사유화라고 비판하며 금남로에서 역대 최대 규모의 보수 성향 집회가 열린 것을 재평가해야 한다고 반박했다。


update! 국민의힘은 민주당의 반응을 광주 정신 사유화라고 비판하며 금남로에서 역대 최대 규모의 보수 성향 집회가 열린 것을 재평가해야 한다고 반박했다. 
60


2025-02-27 13:38:03,222 INFO yield speech len 1.7647165532879818, rtf 1.3830535147510665
2025-02-27 13:38:04,338 INFO yield speech len 1.9969160997732427, rtf 0.5447373481813904
2025-02-27 13:38:05,535 INFO yield speech len 1.9969160997732427, rtf 0.5976930915832865
2025-02-27 13:38:06,792 INFO yield speech len 1.9969160997732427, rtf 0.6278481602473834
2025-02-27 13:38:07,897 INFO yield speech len 1.9969160997732427, rtf 0.5499310799614461
2025-02-27 13:38:09,139 INFO yield speech len 2.507755102040816, rtf 0.4863898347442349
 50%|█████     | 1/2 [00:08<00:08,  8.38s/it]2025-02-27 13:38:09,148 INFO synthesis text 권성동 국민의힘 원내대표는 국회 기자간담회에서 탄핵 반대 집회 자체를 비판할 수는 있어도 광주는 안 된다는 발상은 지역주의와 편가르기 조장이자 반민주적이라고 했다。


update! 권성동 국민의힘 원내대표는 국회 기자간담회에서 탄핵 반대 집회 자체를 비판할 수는 있어도 광주는 안 된다는 발상은 지역주의와 편가르기 조장이자 반민주적이라고 했다. 
66


2025-02-27 13:38:10,809 INFO yield speech len 1.7647165532879818, rtf 0.9413453241761186
2025-02-27 13:38:12,141 INFO yield speech len 1.9969160997732427, rtf 0.6636639082327831
2025-02-27 13:38:13,514 INFO yield speech len 1.9969160997732427, rtf 0.6768956804799652
2025-02-27 13:38:14,560 INFO yield speech len 1.9969160997732427, rtf 0.5158862941032059
2025-02-27 13:38:15,838 INFO yield speech len 1.9969160997732427, rtf 0.6388441719071463
2025-02-27 13:38:17,410 INFO yield speech len 1.9969160997732427, rtf 0.7858674586100807
2025-02-27 13:38:18,683 INFO yield speech len 1.9969160997732427, rtf 0.4505901694904233
2025-02-27 13:38:18,903 INFO yield speech len 0.7082086167800453, rtf 0.30539425731193826
100%|██████████| 2/2 [00:18<00:00,  9.07s/it]


18.363940000534058


In [2]:
import IPython.display as ipd

In [19]:
refer_audio = '/data/minju/TTS/CosyVoice/refer/kyeon_bright_0608_final_01038.wav'
refer_name = refer_audio.split("/")[-1].replace(".wav", "")
print(refer_name)
prompt_speech_16k = load_wav(refer_audio, 16000)
tts_text = "오늘부터 사나흘에 걸쳐 충남과 호남 지역, 제주도 등에 많은 눈이 내리겠습니다. 이 시각 대설주의보가 내려진 전북 고창의 모습을 보면 거리에 눈이 쌓인 가운데 굵은 눈이 펑펑 쏟아지고 있습니다. 서해안에서 강한 눈구름대가 유입되면서 서쪽 지역을 중심으로 눈이 내리고 있습니다."
prompt_text = '이른바 존엄사법으로 불리는 연명의료결정법이 시행되었습니다.'

for i, j in enumerate(cosyvoice.inference_zero_shot(tts_text, prompt_text, prompt_speech_16k, stream=False)):
    torchaudio.save(f'output/{refer_name}_{i}_{tts_text[:3]}.wav'.format(i), j['tts_speech'], cosyvoice.sample_rate)

ipd.Audio(f'output/{refer_name}_{tts_text[:3]}.wav')

kyeon_bright_0608_final_01038


2025-01-07 12:00:55,515 INFO synthesis text 오늘부터 사나흘에 걸쳐 충남과 호남 지역，제주도 등에 많은 눈이 내리겠습니다。이 시각 대설주의보가 내려진 전북 고창의 모습을 보면 거리에 눈이 쌓인 가운데 굵은 눈이 펑펑 쏟아지고 있습니다。
2025-01-07 12:01:03,751 INFO yield speech len 16.0, rtf 0.5147339850664139
2025-01-07 12:01:04,055 INFO synthesis text 서해안에서 강한 눈구름대가 유입되면서 서쪽 지역을 중심으로 눈이 내리고 있습니다。
2025-01-07 12:01:08,258 INFO yield speech len 8.08, rtf 0.5201709447520794
100%|██████████| 2/2 [00:13<00:00,  6.57s/it]


ValueError: rate must be specified when data is a numpy array or list of audio samples.